Wir zeigen zunächst, wie man mit Hilfe von Python Taylorentwicklungen ausrechnen kann.

In [1]:
import sympy
from IPython.display import display
sympy.init_printing(use_latex='mathjax')
import numpy as np
import scipy.special
import math
import matplotlib.pyplot as plt

h=sympy.Symbol("h")
x=sympy.Symbol("x")
f=sympy.Function("f")

In [2]:
# Entwickle die Funktion f um die Stelle 0 in der Variablen h bis zum 5. Glied
display(f(h).series(h,0,5))

                             ⎛  2      ⎞│         ⎛  3      ⎞│         ⎛  4   
                           2 ⎜ d       ⎟│       3 ⎜ d       ⎟│       4 ⎜ d    
                          h ⋅⎜───(f(x))⎟│      h ⋅⎜───(f(x))⎟│      h ⋅⎜───(f(
                             ⎜  2      ⎟│         ⎜  3      ⎟│         ⎜  4   
         ⎛d       ⎞│         ⎝dx       ⎠│x=0      ⎝dx       ⎠│x=0      ⎝dx    
f(0) + h⋅⎜──(f(x))⎟│    + ────────────────── + ────────────────── + ──────────
         ⎝dx      ⎠│x=0           2                    6                    24

   ⎞│           
   ⎟│           
x))⎟│           
   ⎟│           
   ⎠│x=0    ⎛ 5⎞
──────── + O⎝h ⎠
                

In [3]:
# Wir suchen eine Linearkombination aus f(0), f(h), f(-h), die f'(0) möglichst gut approximiert.
# Also:
a=sympy.Symbol("a")
b=sympy.Symbol("b")
c=sympy.Symbol("c")
C=a*f(h).series(h,0,3)+b*f(-h).series(h,0,3)+c*f(0).series(h,0,3)
C=C.simplify()
C=C.factor()
C=C.collect(h)
C=C.simplify()
display(C)

                                      ⎛  2      ⎞│                            
                            2         ⎜ d       ⎟│                            
                           h ⋅(a + b)⋅⎜───(f(x))⎟│                            
                                      ⎜  2      ⎟│                            
          ⎛d       ⎞│                 ⎝dx       ⎠│x=0                         
h⋅(a - b)⋅⎜──(f(x))⎟│    + ────────────────────────── + c⋅f(0) + b⋅f(0) + a⋅f(
          ⎝dx      ⎠│x=0               2                                      

          
          
          
          
      ⎛ 3⎞
0) + O⎝h ⎠
          

Wir erhalten:

\begin{align}
a+b+c=0\\
a-b=1/h\\
a+b=0
\end{align}

Es folgt $c=0$, $a=\frac 1 {2 h}$, $b=-\frac 1 {2 h}$.

Wir testen die resultierende Formel.

In [4]:
C=1/h/2*f(h).series(h,0,4)-1/h/2*f(-h).series(h,0,4)
display(C.simplify())

                    ⎛  3      ⎞│           
                  2 ⎜ d       ⎟│           
                 h ⋅⎜───(f(x))⎟│           
                    ⎜  3      ⎟│           
⎛d       ⎞│         ⎝dx       ⎠│x=0    ⎛ 3⎞
⎜──(f(x))⎟│    + ────────────────── + O⎝h ⎠
⎝dx      ⎠│x=0           6                 

Die Formel ist exakt von der Ordnung 2, aber nicht von der Ordnung 3.

Wir testen die Genauigkeit einiger weiterer Formeln.

In [5]:
# Vorwärts-Differenzenquotient
C=(f(x+h).series(h,0,3)-f(x))/h
display(C.simplify())
# Exakt von der Ordnung 1.

                      ⎛  2        ⎞│            
                      ⎜ d         ⎟│            
                    h⋅⎜────(f(ξ₁))⎟│            
                      ⎜   2       ⎟│            
⎛ d        ⎞│         ⎝dξ₁        ⎠│ξ₁=x    ⎛ 2⎞
⎜───(f(ξ₁))⎟│     + ──────────────────── + O⎝h ⎠
⎝dξ₁       ⎠│ξ₁=x            2                  

In [6]:
# Rückwärts-Differenzenquotient
C=(-f(x-h).series(h,0,3)+f(x))/h
display(C.simplify())
# Exakt von der Ordnung 1.

                      ⎛  2        ⎞│            
                      ⎜ d         ⎟│            
                    h⋅⎜────(f(ξ₁))⎟│            
                      ⎜   2       ⎟│            
⎛ d        ⎞│         ⎝dξ₁        ⎠│ξ₁=x    ⎛ 2⎞
⎜───(f(ξ₁))⎟│     - ──────────────────── + O⎝h ⎠
⎝dξ₁       ⎠│ξ₁=x            2                  

In [7]:
# Zentraler Quotient (siehe oben)
C=((f(x+h/2).series(h,0,4)-f(x-h/2).series(h,0,4)))/h
display(C.simplify())
# Exakt von der Ordnung 2, aber nicht von der Ordnung 3.

                       ⎛  3        ⎞│            
                     2 ⎜ d         ⎟│            
                    h ⋅⎜────(f(ξ₁))⎟│            
                       ⎜   3       ⎟│            
⎛ d        ⎞│          ⎝dξ₁        ⎠│ξ₁=x    ⎛ 3⎞
⎜───(f(ξ₁))⎟│     + ───────────────────── + O⎝h ⎠
⎝dξ₁       ⎠│ξ₁=x             24                 

In [8]:
# Zentraler Quotient für die zweite Ableitung
C=(f(x+h).series(h,0,5)-2*f(x)+f(x-h).series(h,0,5))/(h*h)
display(C.simplify())
# Exakt von der Ordnung 2, aber nicht von der Ordnung 3.

                        ⎛  4        ⎞│            
                      2 ⎜ d         ⎟│            
                     h ⋅⎜────(f(ξ₁))⎟│            
⎛  2        ⎞│          ⎜   4       ⎟│            
⎜ d         ⎟│          ⎝dξ₁        ⎠│ξ₁=x    ⎛ 3⎞
⎜────(f(ξ₁))⎟│     + ───────────────────── + O⎝h ⎠
⎜   2       ⎟│                 12                 
⎝dξ₁        ⎠│ξ₁=x                                